In [7]:
import plotly.express as px
import numpy as np
import pandas as pd
import os
import glob2 as glob
from skimage.measure import label, regionprops, regionprops_table
import open3d as o3d
import plotly.express as px
from aicsimageio import AICSImage
import os
import skimage.io as skio
import plotly.offline as pyo

pyo.init_notebook_mode()

In [8]:
from functions.utilities import path_leaf

data_root = "/Users/nick/Dropbox (Cole Trapnell's Lab)/Nick/pecfin_dynamics/fin_morphodynamics/"
# data_root = "E:\\Nick\\Dropbox (Cole Trapnell's Lab)\\Nick\\pecfin_dynamics\\fin_morphodynamics\\"
date_folder = "20230830"

# get paths to raw data and processed probability stacks
raw_root = os.path.join(data_root, "raw_data", date_folder, "")
built_root = os.path.join(data_root, "built_data", date_folder, "")
nucleus_root = os.path.join(data_root, "nucleus_data", date_folder, "")
if not os.path.isdir(nucleus_root):
    os.makedirs(nucleus_root)

# get metadata from raw file. If there arte multiple .nd2 files in single date folder, we assume that the pixel
# sizes are the same for each
nd2_paths = glob.glob(raw_root + "*.nd2")
imObject = AICSImage(nd2_paths[0])

# extract dimension info and generate a scale reference array
pixel_res_raw = np.asarray(imObject.physical_pixel_sizes)
im_dims = np.asarray([imObject.dims["Z"][0], imObject.dims["Y"][0], imObject.dims["X"][0]])

z_vec = np.flipud(np.arange(im_dims[0]) * pixel_res_raw[0])
y_vec = np.arange(im_dims[1]) * pixel_res_raw[1]
x_vec = np.arange(im_dims[2]) * pixel_res_raw[2]

z_ref_array, y_ref_array, x_ref_array = np.meshgrid(z_vec, y_vec, x_vec, indexing="ij")
#
# get list of datasets with nucleus labels



In [9]:
## import plotly.graph_objects as go

image_list = sorted(glob.glob(built_root + "*_probs.tif"))

prob_thresh = 4
voxel_res = 2

# 
im = 6

prob_path = image_list[im]
prob_name = path_leaf(prob_path)
data_name = prob_name.replace("_prob.tif", "")
# data_name = prob_name.replace("_labels.tif", "")
# save_path = os.path.join(nucleus_root, data_name, '_nucleus_props.csv')

# well number
well_ind = prob_name.find("well")
well_num = int(prob_name[well_ind+4:well_ind+7])

# time step index
time_ind = int(prob_name[well_ind + 9:well_ind+12])

# print('Extracting stats for ' + data_name)
prob_data = skio.imread(prob_path, plugin="tifffile")

# extract 3D positions of each foreground pixel. This is just a high-res point cloud

# nc_z = z_ref_array[np.where(prob_data > 0)]
# nc_y = y_ref_array[np.where(prob_data > 0)]
# nc_x = x_ref_array[np.where(prob_data > 0)]

nc_z = z_ref_array[np.where(prob_data > prob_thresh)]
nc_y = y_ref_array[np.where(prob_data > prob_thresh)]
nc_x = x_ref_array[np.where(prob_data > prob_thresh)]

# Pass xyz to Open3D.o3d.geometry.PointCloud and visualize
xyz_array = np.concatenate((nc_x[:, np.newaxis], nc_y[:, np.newaxis], nc_z[:, np.newaxis]), axis=1)
pcd = o3d.geometry.PointCloud()
pcd.points = o3d.utility.Vector3dVector(xyz_array)
pcd_ds = pcd.voxel_down_sample(voxel_size=voxel_res)
xyz_ds = np.asarray(pcd_ds.points)
        
r_vec = np.sqrt(xyz_ds[:, 0]**2 + xyz_ds[:, 1]**2)

fig = px.scatter_3d(x=xyz_ds[:, 0], y=xyz_ds[:, 1], z=xyz_ds[:, 2], opacity=0.5, color=r_vec)
fig.update_layout(scene=dict(aspectratio=dict(x=1, y=200/350, z=80/350)))
# fig = go.Figure(data=go.Mesh3d(x=xyz_ds[:, 0], y=xyz_ds[:, 1], z=-xyz_ds[:, 2], opacity=0.1))
fig.show()

In [ ]:
# def boundary(mesh, close_paths=True):
#     # Set of all edges and of boundary edges (those that appear only once).
#     edge_set = set()
#     boundary_edges = set()

#     # Iterate over all edges, as tuples in the form (i, j) (sorted with i < j to remove ambiguities).
#     # For each edge, three cases are possible:
#     # 1. The edge has never been visited before. In this case, we can add it to the edge set and as a boundary
#     #    candidate as well.
#     # 2. The edge had already been visited once. We want to keep it into the set of all edges but remove it from the
#     #    boundary set.
#     # 3. The edge had already been visited at least twice. This is generally an indication that there is an issue with
#     #    the mesh. More precisely, it is not a manifold, and boundaries are not closed-loops.
#     for e in map(tuple, mesh.edges_sorted):
#         if e not in edge_set:
#             edge_set.add(e)
#             boundary_edges.add(e)
#         elif e in boundary_edges:
#             boundary_edges.remove(e)
#         else:
#             raise RuntimeError(f"The mesh is not a manifold: edge {e} appears more than twice.")

#     # Given all boundary vertices, we create a simple dictionary that tells who are their neighbours.
#     neighbours = dict(lambda: [])
#     for v1, v2 in boundary_edges:
#         neighbours[v1].append(v2)
#         neighbours[v2].append(v1)

#     # We now look for all boundary paths by "extracting" one loop at a time. After obtaining a path, we remove its edges
#     # from the "boundary_edges" set. The algorithm terminates when all edges have been used.
#     boundary_paths = []
#     boundary_vertices = []

#     while len(boundary_edges) > 0:
#         # Given the set of remaining boundary edges, get one of them and use it to start the current boundary path.
#         # In the sequel, v_previous and v_current represent the edge that we are currently processing.
#         v_previous, v_current = next(iter(boundary_edges))
#         boundary_vertices = [v_previous]

#         # Keep iterating until we close the current boundary curve (the "next" vertex is the same as the first one).
#         while v_current != boundary_vertices[0]:
#             # We grow the path by adding the vertex "v_current".
#             boundary_vertices.append(v_current)

#             # We now check which is the next vertex to visit.
#             v1, v2 = neighbours[v_current]
#             if v1 != v_previous:
#                 v_current, v_previous = v1, v_current
#             elif v2 != v_previous:
#                 v_current, v_previous = v2, v_current
#             else:
#                 # This line should be un-reachable. I am keeping it only to detect bugs in case I made a mistake when
#                 # designing the algorithm.
#                 raise RuntimeError(f"Next vertices to visit ({v1=}, {v2=}) are both equal to {v_previous=}.")

#         # Close the path (by repeating the first vertex) if needed.
#         if close_paths:
#             boundary_vertices.append(boundary_vertices[0])

#         # "Convert" the vertices from indices to actual Cartesian coordinates.
#         boundary_paths.append(mesh.vertices[boundary_vertices])
#         boundary_vertices.append(boundary_vertices)

#         # Remove all boundary edges that were added to the last path.
#         boundary_edges = set(e for e in boundary_edges if e[0] not in boundary_vertices)

#     # Return the list of boundary paths.
#     return boundary_paths, boudnary_vertices

In [ ]:
import alphashape

ft_indices = np.where(r_vec>=150)
points = xyz_ds / np.max(xyz_ds)
alpha = 20 # 0.95 * alphashape.optimizealpha(points)
hull10 = alphashape.alphashape(points, 10)
hull20 = alphashape.alphashape(points, 20)
hull30 = alphashape.alphashape(points, 30)


In [ ]:

# fig = px.scatter_3d(x=outline[:, 0], y=outline[:, 1], z=outline[:, 2], color=outline[:, 2])
fig = go.Figure(data=go.Mesh3d(x=hull10.vertices[:, 0], y=hull10.vertices[:, 1],z=hull10.vertices[:, 2], opacity=0.5,
                               i=hull10.faces[:, 0], j=hull10.faces[:, 1], k=hull10.faces[:, 2]))
fig.add_trace(go.Mesh3d(x=hull20.vertices[:, 0], y=hull20.vertices[:, 1],z=hull20.vertices[:, 2], opacity=0.5,
                               i=hull20.faces[:, 0], j=hull20.faces[:, 1], k=hull20.faces[:, 2]))
fig.add_trace(go.Mesh3d(x=hull30.vertices[:, 0], y=hull30.vertices[:, 1],z=hull30.vertices[:, 2], opacity=0.5,
                               i=hull30.faces[:, 0], j=hull30.faces[:, 1], k=hull30.faces[:, 2]))

fig.update_layout(scene=dict(aspectratio=dict(x=1, y=200/350, z=80/350)))
# fig = go.Figure(data=go.Mesh3d(x=xyz_ds[ft_indices[0], 0], y=xyz_ds[ft_indices[0], 1], 
#                                 z=xyz_ds[ft_indices[0], 2], alphahull=10, opacity=0.5))
fig.show()

In [ ]:
import matplotlib.pyplot as plt
from mpl_toolkits.mplot3d import Axes3D

fig = plt.figure()
ax = fig.add_subplot(111, projection='3d')
ax.plot_trisurf(-hull.vertices[:, 0], -hull.vertices[:,1], triangles=hull.faces, Z=hull.vertices[:,2]) 
plt.show()

In [ ]:
outline